## 기본 세팅/ 전처리

In [1]:
import pandas as pd
import geopandas as gpd

In [2]:
import fiona #공간데이터를 딕셔너리 형태 등으로 접근할 수 있는 라이브러리 
from fiona.crs import from_epsg # 좌표변환 

import pyproj  # 좌표변환
from pyproj import Proj, transform

In [3]:
df = pd.read_csv('./data/pop/2016년+3월+SKT이동통신을+이용한+성별연령별+유동인구(종로구).csv', index_col=None, header=0, 
                          names=['STD_YM', 'SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'X_COORD', 'Y_COORD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU', 'DATA_LOAD_DT'], 
                          usecols=['SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'X_COORD', 'Y_COORD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU'],
                          dtype={'BLOCK_CD':object, 'Y_COORD':float}, #지정안하고 로딩시 나머지 항목은 잘 인식해서...2개만 지정함
                 encoding="utf-8", 
                 delimiter=',' , #항목 구분자 '\t'
                 thousands = ',' ) #천단위 쉼표 제거   
df.info() #행 수 및 컬럼 정보 df.shape()을 이용해도 됨
df.head() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5667 entries, 0 to 5666
Data columns (total 18 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   SI_DO_NM                5667 non-null   object 
 1   SGNG_NM                 5667 non-null   object 
 2   ADONG_NM                5667 non-null   object 
 3   BLOCK_CD                5667 non-null   object 
 4   X_COORD                 5667 non-null   float64
 5   Y_COORD                 5667 non-null   float64
 6   MAN_FLOW_POP_CNT_10G    5667 non-null   float64
 7   MAN_FLOW_POP_CNT_20G    5667 non-null   float64
 8   MAN_FLOW_POP_CNT_30G    5667 non-null   float64
 9   MAN_FLOW_POP_CNT_40G    5667 non-null   float64
 10  MAN_FLOW_POP_CNT_50G    5667 non-null   float64
 11  MAN_FLOW_POP_CNT_60GU   5667 non-null   float64
 12  WMAN_FLOW_POP_CNT_10G   5667 non-null   float64
 13  WMAN_FLOW_POP_CNT_20G   5667 non-null   float64
 14  WMAN_FLOW_POP_CNT_30G   5667 non-null   

SI_DO_NM SGNG_NM ADONG_NM              BLOCK_CD     X_COORD    Y_COORD  \
0    서울특별시     종로구      평창동  11010560200141000001  952559.000  1956707.0   
1    서울특별시     종로구      평창동  11010560200141000001  952608.375  1956758.0   
2    서울특별시     종로구      평창동  11010560200141000001  952609.625  1956963.0   
3    서울특별시     종로구      평창동  11010560200141000001  952757.500  1957117.0   
4    서울특별시     종로구      평창동  11010560200051000001  954573.375  1957415.0   

   MAN_FLOW_POP_CNT_10G  MAN_FLOW_POP_CNT_20G  MAN_FLOW_POP_CNT_30G  \
0                  3.63                  4.67                  6.56   
1                  4.01                  5.18                  7.30   
2                  1.05                  1.76                  1.43   
3                  2.76                  3.43                  4.82   
4                  1.44                  1.50                  2.78   

   MAN_FLOW_POP_CNT_40G  MAN_FLOW_POP_CNT_50G  MAN_FLOW_POP_CNT_60GU  \
0                  8.24                  9.03                   7.77   
1                  9.16                 10.00                   8.64   
2                  1.73                  1.58                   1.55   
3                  6.07                  6.58                   5.83   
4                  3.90                  3.47                   2.96   

   WMAN_FLOW_POP_CNT_10G  WMAN_FLOW_POP_CNT_20G  WMAN_FLOW_POP_CNT_30G  \
0                   6.07                   4.44                   7.41   
1                   6.71                   4.94                   8.24   
2                   1.41                   1.79                   2.10   
3                   4.81                   3.17                   5.51   
4                   0.97                   1.75                   2.78   

   WMAN_FLOW_POP_CNT_40G  WMAN_FLOW_POP_CNT_50G  WMAN_FLOW_POP_CNT_60GU  
0                  11.23                  10.50                    8.34  
1                  12.46                  11.64                    9.25  
2                   2.53                   2.05                    2.00  
3                   8.48                   7.86                    6.29  
4                   3.75                   3.71                    3.36

In [4]:
# 레코드별 총인구, 남자 인구, 여자 인구 
# 노트패드에서 CSV 헤더의 TAB 공간을 "" + df."로 일괄 바꾸기 함 
df['POP_ALL'] = df.MAN_FLOW_POP_CNT_10G + df.MAN_FLOW_POP_CNT_20G + df.MAN_FLOW_POP_CNT_30G + df.MAN_FLOW_POP_CNT_40G + df.MAN_FLOW_POP_CNT_50G + df.MAN_FLOW_POP_CNT_60GU + df.WMAN_FLOW_POP_CNT_10G + df.WMAN_FLOW_POP_CNT_20G + df.WMAN_FLOW_POP_CNT_30G + df.WMAN_FLOW_POP_CNT_40G + df.WMAN_FLOW_POP_CNT_50G + df.WMAN_FLOW_POP_CNT_60GU

In [5]:
#불필요한 항목 제거
df.drop(['SI_DO_NM', 'SGNG_NM', 'ADONG_NM', 'BLOCK_CD', 'MAN_FLOW_POP_CNT_10G', 'MAN_FLOW_POP_CNT_20G', 'MAN_FLOW_POP_CNT_30G', 'MAN_FLOW_POP_CNT_40G', 'MAN_FLOW_POP_CNT_50G', 'MAN_FLOW_POP_CNT_60GU', 'WMAN_FLOW_POP_CNT_10G', 'WMAN_FLOW_POP_CNT_20G', 'WMAN_FLOW_POP_CNT_30G', 'WMAN_FLOW_POP_CNT_40G', 'WMAN_FLOW_POP_CNT_50G', 'WMAN_FLOW_POP_CNT_60GU'], axis=1, inplace=True)

In [6]:
#이상치 제거
import numpy as np
from scipy.stats import zscore
df['pop_zscore'] = zscore(df['POP_ALL'])
threshold = 3 #2는 약 95%, 3을 적용하면 약 99.73%
df['outliers'] = np.where((df['pop_zscore'] - threshold > 0), True, np.where(df['pop_zscore'] + threshold < 0, True, False))
df.drop(df[df['outliers'] == True].index,inplace=True)
df.info()
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5596 entries, 0 to 5666
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   X_COORD     5596 non-null   float64
 1   Y_COORD     5596 non-null   float64
 2   POP_ALL     5596 non-null   float64
 3   pop_zscore  5596 non-null   float64
 4   outliers    5596 non-null   bool   
dtypes: bool(1), float64(4)
memory usage: 224.1 KB


X_COORD    Y_COORD  POP_ALL  pop_zscore  outliers
0  952559.000  1956707.0    87.89   -0.373183     False
1  952608.375  1956758.0    97.53   -0.354854     False
2  952609.625  1956963.0    20.98   -0.500400     False
3  952757.500  1957117.0    65.61   -0.415544     False
4  954573.375  1957415.0    32.37   -0.478744     False

In [7]:
# 좌표 속성을 가지고 지오메트리 데이터를 생성
geom_df = gpd.points_from_xy(df.X_COORD, df.Y_COORD)

In [8]:
# 기존의 데이터프레임 컬럼명을 가져옴 
columns = df.columns

In [9]:
# 속성 데이터프레임에 Geometry를 붙여서 공간 데이터프레임을 생성 
gdf_pop_5179 = gpd.GeoDataFrame(df[columns], geometry=geom_df, crs=from_epsg(5179))
gdf_pop_5179.head()

C:\Users\dhl\AppData\Roaming\Python\Python38\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


X_COORD    Y_COORD  POP_ALL  pop_zscore  outliers  \
0  952559.000  1956707.0    87.89   -0.373183     False   
1  952608.375  1956758.0    97.53   -0.354854     False   
2  952609.625  1956963.0    20.98   -0.500400     False   
3  952757.500  1957117.0    65.61   -0.415544     False   
4  954573.375  1957415.0    32.37   -0.478744     False   

                         geometry  
0  POINT (952559.000 1956707.000)  
1  POINT (952608.375 1956758.000)  
2  POINT (952609.625 1956963.000)  
3  POINT (952757.500 1957117.000)  
4  POINT (954573.375 1957415.000)

In [10]:
# 좌표계 변환
gdf_pop_5179.crs = {'init' :'epsg:5179'}
gdf_pop_4326 = gdf_pop_5179.to_crs('epsg:4326')

C:\Users\dhl\AppData\Roaming\Python\Python38\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


In [11]:
# Geometry를 이용하여 X, Y 좌표 항목을 생성 
gdf_pop_4326["lon"] = gdf_pop_4326.geometry.x
gdf_pop_4326["lat"] = gdf_pop_4326.geometry.y
gdf_pop_4326.head()

X_COORD    Y_COORD  POP_ALL  pop_zscore  outliers  \
0  952559.000  1956707.0    87.89   -0.373183     False   
1  952608.375  1956758.0    97.53   -0.354854     False   
2  952609.625  1956963.0    20.98   -0.500400     False   
3  952757.500  1957117.0    65.61   -0.415544     False   
4  954573.375  1957415.0    32.37   -0.478744     False   

                     geometry         lon        lat  
0  POINT (126.96250 37.60857)  126.962500  37.608568  
1  POINT (126.96306 37.60903)  126.963056  37.609030  
2  POINT (126.96306 37.61088)  126.963057  37.610877  
3  POINT (126.96472 37.61227)  126.964722  37.612273  
4  POINT (126.98528 37.61505)  126.985277  37.615051

## Plotly (with Mapbox)

In [12]:
# mapbox token 정보 읽기 
f = open('../../etc/mapbox.txt', 'r')
lines = f.readlines()
mapbox_token = lines[0]

In [13]:
#MAPBOX_API_KEY = mapbox_token.replace("'","")  #문자열의 홑따옴표 제거
MAPBOX_API_KEY2 = mapbox_token.replace('"','')  #문자열의 쌍따옴표 제거

In [16]:
import plotly.express as px  #pip install plotly
from IPython.display import IFrame

In [28]:
px.set_mapbox_access_token(MAPBOX_API_KEY2)
df = gdf_pop_4326

fig = px.scatter_mapbox(df, lat="lat", lon="lon", size_max=15, zoom=11, color="POP_ALL", 
                        size="POP_ALL", #이 파라미터의 주석 전후 비교 
                        color_continuous_scale=px.colors.cyclical.IceFire)

fig.show()

In [95]:
# shp 로딩
gdf_dong = gpd.read_file('./data/gdf_dong.shp', encoding='utf-8', crs='epsg:4326')  #euc-kr, euckr, utf-8, cp949 중 선택
gdf_dong.crs  #좌표계 확인용 

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [96]:
gdf_dong2 = gdf_dong[ gdf_dong.sido == '11']
gdf_dong2['area'] = gdf_dong2.geometry.area * 10000 #임의로 값을 올려줌
gdf_dong2.head()

<ipython-input-96-e725a5ef724c>:2: UserWarning:

Geometry is in a geographic CRS. Results from 'area' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.




OBJECTID         adm_nm   adm_cd     adm_cd2    sgg sido sidonm sggnm  \
0         1  서울특별시 종로구 사직동  1101053  1111053000  11110   11  서울특별시   종로구   
1         2  서울특별시 종로구 삼청동  1101054  1111054000  11110   11  서울특별시   종로구   
2         3  서울특별시 종로구 부암동  1101055  1111055000  11110   11  서울특별시   종로구   
3         4  서울특별시 종로구 평창동  1101056  1111056000  11110   11  서울특별시   종로구   
4         5  서울특별시 종로구 무악동  1101057  1111057000  11110   11  서울특별시   종로구   

                                            geometry      area  
0  POLYGON ((126.97689 37.57565, 126.97703 37.569...  1.189027  
1  POLYGON ((126.98269 37.59507, 126.98337 37.594...  1.388847  
2  POLYGON ((126.97585 37.59656, 126.97359 37.593...  2.246651  
3  POLYGON ((126.97507 37.63139, 126.97649 37.630...  9.201969  
4  POLYGON ((126.96067 37.58080, 126.96281 37.579...  0.476927

In [97]:
# 동별 경계를 geojson으로 저장
gdf_dong2.to_file("./data/gdf_dong2.geojson", driver='GeoJSON', encoding='utf-8')

In [98]:
import json

with open('./data/gdf_dong2.geojson', encoding='utf-8') as f:
    json_dong = json.load(f)

In [76]:
# json 구조 검토
json_dong["features"][0].keys()

dict_keys(['type', 'properties', 'geometry'])

In [77]:
# json 속성 항목 검토
json_dong["features"][0]['properties'].keys()

dict_keys(['OBJECTID', 'adm_nm', 'adm_cd', 'adm_cd2', 'sgg', 'sido', 'sidonm', 'sggnm', 'area'])

In [78]:
# json 첫번째 레코드의 도형 좌표
json_dong["features"][0]['geometry']['coordinates'][0][0]

[126.97688884274817, 37.575650779448786]

In [91]:
# json 전체 정보
json_dong

{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'OBJECTID': 1,
    'adm_nm': '서울특별시 종로구 사직동',
    'adm_cd': '1101053',
    'adm_cd2': '1111053000',
    'sgg': '11110',
    'sido': '11',
    'sidonm': '서울특별시',
    'sggnm': '종로구',
    'area': 1.1890266469269883},
   'geometry': {'type': 'Polygon',
    'coordinates': [array([[126.98,  37.58],
            [126.98,  37.57],
            [126.98,  37.57],
            [126.98,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.97,  37.57],
            [126.96,  37.58],
            [126.96,  37.58],
            [126.96,  37.58],
            [126.96,  37.58],
            [126.97,  37.58],
            [126.97,  37.58],

In [99]:
min_area = gdf_dong2['area'].min()
max_area = gdf_dong2['area'].max()

In [103]:
# json 데이터를 활용한 Choropleth Map
fig = px.choropleth_mapbox(gdf_dong2, geojson=json_dong, locations=gdf_dong2.OBJECTID, featureidkey="properties.OBJECTID",
                           color='area', color_continuous_scale="Viridis",
                           range_color=(min_area, max_area),
                           mapbox_style="carto-positron",
                           zoom=10, center = {"lat": 37.57, "lon": 127.0},
                           opacity=0.5,
                           labels={'area'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

- Mapbox 배경지도 종류  
open-street-map  
carto-positron  
carto-darkmatter  
stamen-terrain  
stamen-toner  
stamen-watercolor  


In [122]:
# geodataframe을 활용한 Choropleth Map
fig = px.choropleth_mapbox(gdf_dong2, geojson=gdf_dong2.geometry, locations=gdf_dong2.index, 
                           color='area', color_continuous_scale="Viridis",
                           range_color=(min_area, max_area),
                           mapbox_style="carto-positron",
                           zoom=10, center = {"lat": 37.57, "lon": 127.0},
                           opacity=0.5,
                           labels={'area'}
                          )

fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "United States Geological Survey",
            "source": ["http://xdworld.vworld.kr:8080/2d/gray/service/{z}/{x}/{y}.png" ]
        }
      ])

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

### plotly 참조  

https://plotly.com/python/mapbox-county-choropleth/   

https://plotly.com/python/mapbox-layers/  

https://plotly.com/python/colorscales/   

https://plotly.com/python/builtin-colorscales/    

https://plotly.com/python/animations/   